In [1]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from webdriver_manager.chrome import ChromeDriverManager
import time
import pandas as pd
from bs4 import BeautifulSoup
import re

In [2]:
# Khởi tạo trình duyệt Chrome
options = webdriver.ChromeOptions()
options.add_argument("--start-maximized") 
options.add_argument("--disable-blink-features=AutomationControlled")  
service = Service(ChromeDriverManager().install())
driver = webdriver.Chrome(service=service, options=options)

In [3]:
# Đọc file CSV chứa các link và category đã crawl trước đó
input_csv = "D:/BaiDoAnChuyenNganh3/Automated-Resume-Ranking-System-main/csvfiles/crawlcv/crawldata2links_examples.csv"  # File CSV từ bước crawl trước
df_links = pd.read_csv(input_csv)

In [4]:
# Khởi tạo danh sách để lưu dữ liệu mới
data = []

In [5]:
# Hàm định dạng văn bản (email, số điện thoại, khoảng cách)
def format_text(text):
    # Loại bỏ khoảng trắng thừa
    text = re.sub(r'\s+', ' ', text).strip()
    
    # Định dạng số điện thoại (ví dụ: (555) 555-5555)
    phone_pattern = r'\(?\d{3}\)?\s*-?\s*\d{3}\s*-?\s*\d{4}'
    phone_matches = re.findall(phone_pattern, text)
    for phone in phone_matches:
        # Chuẩn hóa số điện thoại thành dạng (555) 555-5555
        phone_clean = re.sub(r'\D', '', phone)  # Loại bỏ ký tự không phải số
        formatted_phone = f"({phone_clean[:3]}) {phone_clean[3:6]}-{phone_clean[6:]}"
        text = text.replace(phone, formatted_phone)
    
    # Định dạng email (đảm bảo không có khoảng trắng thừa)
    email_pattern = r'[\w\.-]+@[\w\.-]+\.\w+'
    email_matches = re.findall(email_pattern, text)
    for email in email_matches:
        text = text.replace(email, email.strip())
    
    # Định dạng địa chỉ (thêm khoảng cách hợp lý)
    address_pattern = r'[A-Za-z\s]+,\s*[A-Za-z\s]+,\s*[A-Za-z\s]+,\s*\d{5}'
    address_matches = re.findall(address_pattern, text)
    for address in address_matches:
        formatted_address = address.replace(',', ', ')
        text = text.replace(address, formatted_address)
    
    # Thêm dòng mới giữa các đoạn
    text = re.sub(r'\n\s*\n+', '\n', text)  # Loại bỏ dòng trống thừa
    return text

# Duyệt qua từng link trong file CSV
for index, row in df_links.iterrows():
    resume_link = row["resume_link"]
    category = row["Category"]
    print(f"Đang crawl: {resume_link}")

    try:
        # Truy cập link
        driver.get(resume_link)
        time.sleep(2)  # Chờ trang tải

        # Tìm thẻ div class="blog-main__wrapper"
        wrapper = driver.find_element(By.CLASS_NAME, "blog-main__wrapper")
        # Tìm thẻ div class="blog-main blog-main--en"
        blog_main = wrapper.find_element(By.CLASS_NAME, "blog-main.blog-main--en")
        # Tìm thẻ div class="b-section b-section--fixed-width" với style cụ thể
        section = blog_main.find_element(By.CSS_SELECTOR, "div.b-section.b-section--fixed-width[style*='background-color: #fafafa']")

        # Lấy nội dung văn bản từ các thẻ p và ul li
        resume_str = ""
        p_tags = section.find_elements(By.TAG_NAME, "p")
        for p in p_tags:
            text = format_text(p.text)
            if text:  # Chỉ thêm nếu có nội dung
                resume_str += text + "\n"

        ul_tags = section.find_elements(By.TAG_NAME, "ul")
        for ul in ul_tags:
            li_tags = ul.find_elements(By.TAG_NAME, "li")
            for li in li_tags:
                text = format_text(li.text)
                if text:
                    resume_str += text + "\n"

        # Lấy toàn bộ HTML của section
        resume_html = section.get_attribute("outerHTML")

        # Thêm dữ liệu vào danh sách
        data.append({
            "ID": index + 1,  # ID bắt đầu từ 1
            "resume_str": resume_str.strip(),
            "resume_html": resume_html,
            "Category": category
        })

    except Exception as e:
        print(f"Lỗi khi crawl {resume_link}: {e}")

Đang crawl: https://zety.com/blog/accounting-resume-example
Đang crawl: https://zety.com/blog/accounting-assistant-resume-example
Đang crawl: https://zety.com/blog/accounting-clerk-resume-example
Đang crawl: https://zety.com/blog/accounting-manager-resume-example
Đang crawl: https://zety.com/blog/accounts-payable-resume-example
Đang crawl: https://zety.com/blog/accounts-receivable-resume-example
Đang crawl: https://zety.com/blog/accounts-receivable-resume-example
Đang crawl: https://zety.com/blog/actuary-resume-example
Đang crawl: https://zety.com/blog/audit-associate-resume-example
Đang crawl: https://zety.com/blog/auditor-resume-example
Đang crawl: https://zety.com/blog/bank-manager-resume-example
Đang crawl: https://zety.com/blog/bank-teller-resume
Đang crawl: https://zety.com/blog/banking-resume-example
Đang crawl: https://zety.com/blog/billing-specialist-resume-example
Đang crawl: https://zety.com/blog/bookkeeper-resume-example
Đang crawl: https://zety.com/blog/branch-manager-resu

In [9]:
# In dữ liệu theo dạng dọc để kiểm tra
print("Dữ liệu crawl được:")
for item in data:
    print(f"ID: {item['ID']}")
    print(f"resume_str:\n{item['resume_str']}")
    print(f"resume_html:\n{item['resume_html']}")
    print(f"Category: {item['Category']}")
    print("-" * 50)  # Dòng phân cách giữa các mục

Dữ liệu crawl được:
ID: 1
resume_str:
Gerard Levine
Certified Public Accountant
+1-(123) 456-7890
gerardlevine@email.com
linkedin.com/in/gerardlevine
Summary
Certified Public Accountant with 5+ years of experience in ledger processes, account reconciliations and streamlining accounts. Seeking to assist NovaGen Corporation in creating optimized financial solutions. Reduced annual budget costs by 10% at Radiant Innovations by restructuring my team’s organization, optimizing their performance and time management.
Experience
Senior Accountant
Radiant Innovations, Kenosha, WI
July 2022–Present
Key Qualifications & Responsibilities
Key Achievement:
Junior Accountant
Quest Industries, Kenosha, WI
June 2019–June 2022
Key Qualifications & Responsibilities
Key Achievement:
Education
Bachelor of Science in Accounting
University of Wisconsin, WI
August 2015–May 2019
Relevant extracurricular activities
Academic achievements
Skills
Certifications
Awards
Memberships
Member of the American Institute o

In [7]:
# Đóng trình duyệt
driver.quit()

In [8]:
# Chuyển dữ liệu thành DataFrame và lưu vào file CSV
if data:
    df = pd.DataFrame(data)
    df.to_csv("D:/BaiDoAnChuyenNganh3/Automated-Resume-Ranking-System-main/csvfiles/crawlcv/finaldata2links_examples.csv", index=False, encoding="utf-8")
    print(f"Dữ liệu đã được crawl và lưu vào file cv_details.csv với {len(data)} mục")
else:
    print("Không có dữ liệu nào được crawl!")

Dữ liệu đã được crawl và lưu vào file cv_details.csv với 774 mục
